# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [TRPO]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

fatal: destination path 'RL_VPP_Thesis' already exists and is not an empty directory.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          __pycache__/          trained_models/
data/                             README.md             VPP_environment.py
Hyperparameters_sweep_notebooks/  RL_VPP_Thesis/        VPP_simulator.ipynb
log.log                           Simulator_notebooks/  wandb/


In [ ]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import TRPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')
wandb, version 0.13.4


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f191bd81cd0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21138.89 , over-consume=kWh  38202.18 , under-consume=kWh  17063.3 , Total_cost=€  815.67 , overcost=€  1319.95 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/TRPO_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/TRPO_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="Simulator_notebooks/TRPO_VPP_simulator.ipynb"


In [ ]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/TRPO_models/model_TRPO_"

model_id = "2ydih28d"
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21440.37 , over-consume=kWh  38601.58 , under-consume=kWh  17161.21 , Total_cost=€  901.07 , overcost=€  1387.3 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -5459.44 , over-consume=KWh  1618.95 , under-consume=KWh  7078.39 , Total_cost=€  -128.05 , Overcost=€  54.06 
 EV_INFO: Av.EV_energy_leaving=kWh  65.02 , Std.EV_energy_leaving=kWh  27.4 , EV_departures =  1042 , EV_queue_left =  1
SCORE:  Cumulative_reward= 352798.88 - Step_rewars (load_t= 333853.99, EVs_energy_t= -2717.82)
 - Final_rewards (EVs_energy= 13945.15, Overconsume= -895.51, Underconsume= -3983.71, Overcost= 12596.78)
Episode:1 Score:352798.87758907746


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  37.583965  52.190071  45.174614  56.490974   
2022-01-01 00:15:00  37.288353  51.894459  44.879002  56.740974   
2022-01-01 00:30:00  37.013596  51.619701  44.604244  56.990974   
2022-01-01 00:45:00  36.763596  51.369701  44.354244  57.240974   
2022-01-01 01:00:00  36.513596  51.119701  44.104244  57.490974   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00   0.000000   0.000000  97.810760  69.494698   
2022-06-06 05:00:00   0.000000   0.000000  99.360207  71.044144   
2022-06-06 05:15:00   0.000000   0.000000  99.989998  72.553444   
2022-06-06 05:30:00   0.000000   0.000000  99.989998  74.046646   
2022-06-06 05:45:00   0.000000   0.000000  99.989998  75.470108   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 2, 2, 1]   
2022-01-01 00:15:00  [3126, 3127, 3124, 3125]  [2, 2, 2, 1]   
2022-01-01 00:30:00  [3126, 3127, 3124, 3125]  [2, 2, 2, 1]   
2022-01-01 00:45:00  [3126, 3127, 3124, 3125]  [2, 2, 2, 1]   
2022-01-01 01:00:00  [3126, 3127, 3124, 3125]  [2, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00        [0, 0, 3595, 3596]  [0, 0, 1, 1]   
2022-06-06 05:00:00        [0, 0, 3595, 3596]  [0, 0, 1, 1]   
2022-06-06 05:15:00        [0, 0, 3595, 3596]  [0, 0, 1, 1]   
2022-06-06 05:30:00        [0, 0, 3595, 3596]  [0, 0, 1, 1]   
2022-06-06 05:45:00        [0, 0, 3595, 3596]  [0, 0, 1, 1]   

                                       mask_truth      load  load_reward  \
time                                                                       
2022-01-01 00:00:00  [False, False, False, False]  1.003257    15.000000   
2022-01-01 00:15:00     [True, True, True, False]  0.000000    15.000000   
2022-01-01 00:30:00     [True, True, True, False]  0.000000    -0.040485   
2022-01-01 00:45:00     [True, True, True, False] -1.024291    10.370408   
2022-01-01 01:00:00     [True, True, True, False] -0.308639    11.837808   
...                                           ...       ...          ...   
2022-06-06 04:45:00     [True, True, False, True]  0.000000    15.000000   
2022-06-06 05:00:00     [True, True, False, True]  0.000000    -4.196705   
2022-06-06 05:15:00     [True, True, False, True] -3.518023    -6.793448   
2022-06-06 05:30:00     [True, True, False, True] -5.972793    -6.539857   
2022-06-06 05:45:00     [True, True, False, True] -5.693843    -6.765473   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  15.000000  
2022-01-01 00:15:00        0.0  15.000000  
2022-01-01 00:30:00        0.0  -0.040485  
2022-01-01 00:45:00        0.0  10.370408  
2022-01-01 01:00:00        0.0  11.837808  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  -4.196705  
2022-06-06 05:15:00        0.0  -6.793448  
2022-06-06 05:30:00        0.0  -6.539857  
2022-06-06 05:45:00        0.0  -6.765473  

[15000 rows x 11 columns]

In [ ]:
#env.plot_Elvis_results()

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 02:45:00, Parking_time: 24, Leaving_time: 2022-01-02 02:45:00, SOC: 0.4385788254616059, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 19:30:00, Parking_time: 22.923220787268423, Leaving_time: 2023-01-01 18:25:23.594834, SOC: 0.48720495785270057, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12655.56 , over-consume=kWh  34035.17 , under-consume=kWh  21379.61 , Total_cost=€  609.95 , overcost=€  1476.93 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12813.17 , over-consume=kWh  34560.85 , under-consume=kWh  21747.69 , Total_cost=€  638.11 , overcost=€  1521.69 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7718.1 , over-consume=KWh  1235.72 , under-consume=KWh  8953.81 , Total_cost=€  -299.1 , Overcost=€  53.03 
 EV_INFO: Av.EV_energy_leaving=kWh  71.57 , Std.EV_energy_leaving=kWh  26.6 , EV_departures =  1039 , EV_queue_left =  0
SCORE:  Cumulative_reward= 359737.51 - Step_rewars (load_t= 314137.59, EVs_energy_t= 18906.93)
 - Final_rewards (EVs_energy= 17926.61, Overconsume= -643.05, Underconsume= -3969.63, Overcost= 13379.06)
Episode:1 Score:359737.50661767425


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0    1    2    3           EVs_id       actions  \
time                                                                           
2022-01-01 00:00:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:15:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:30:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:45:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 01:00:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [1, 0, 2, 1]   
...                        ...  ...  ...  ...              ...           ...   
2022-06-06 04:45:00  87.895882  0.0  0.0  0.0  [6708, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 05:00:00  90.645882  0.0  0.0  0.0  [6708, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 05:15:00  93.395882  0.0  0.0  0.0  [6708, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 05:30:00  96.145882  0.0  0.0  0.0  [6708, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 05:45:00  98.895882  0.0  0.0  0.0  [6708, 0, 0, 0]  [1, 0, 0, 0]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, True, False, False] -3.421043    -4.262864   
2022-01-01 00:15:00  [False, True, False, False] -3.557718    -5.156515   
2022-01-01 00:30:00  [False, True, False, False] -4.172167    -4.241133   
2022-01-01 00:45:00  [False, True, False, False] -3.544680    -6.180056   
2022-01-01 01:00:00  [False, True, False, False] -5.298061    -5.175662   
...                                          ...       ...          ...   
2022-06-06 04:45:00     [True, True, True, True] -0.183576    -4.912283   
2022-06-06 05:00:00     [True, True, True, True] -3.947370    -2.720052   
2022-06-06 05:15:00     [True, True, True, True] -2.632031    -4.822778   
2022-06-06 05:30:00     [True, True, True, True] -3.893667    -3.411844   
2022-06-06 05:45:00     [True, True, True, True] -3.047106   -10.888283   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.262864  
2022-01-01 00:15:00        0.0  -5.156515  
2022-01-01 00:30:00        0.0  -4.241133  
2022-01-01 00:45:00        0.0  -6.180056  
2022-01-01 01:00:00        0.0  -5.175662  
...                        ...        ...  
2022-06-06 04:45:00        0.0  -4.912283  
2022-06-06 05:00:00        0.0  -2.720052  
2022-06-06 05:15:00        0.0  -4.822778  
2022-06-06 05:30:00        0.0  -3.411844  
2022-06-06 05:45:00        0.0 -10.888283  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 06:45:00, Parking_time: 24, Leaving_time: 2022-01-02 06:45:00, SOC: 0.43100644190786686, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 20:00:00, Parking_time: 24, Leaving_time: 2023-01-01 20:00:00, SOC: 0.5923449419913698, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  9050.11 , over-consume=kWh  32438.17 , under-consume=kWh  23388.06 , Total_cost=€  505.76 , overcost=€  1357.45 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8749.81 , over-consume=kWh  32160.28 , under-consume=kWh  23410.47 , Total_cost=€  456.94 , overcost=€  1322.94 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9004.56 , over-consume=KWh  1099.28 , under-consume=KWh  10103.83 , Total_cost=€  -327.09 , Overcost=€  44.11 
 EV_INFO: Av.EV_energy_leaving=kWh  74.28 , Std.EV_energy_leaving=kWh  25.47 , EV_departures =  1038 , EV_queue_left =  1
SCORE:  Cumulative_reward= 354874.54 - Step_rewars (load_t= 301395.18, EVs_energy_t= 26341.64)
 - Final_rewards (EVs_energy= 18394.37, Overconsume= -578.83, Underconsume= -4342.4, Overcost= 13664.59)
Episode:1 Score:354874.54055349197


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                        
2022-01-01 00:00:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 00:15:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 00:30:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 00:45:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 01:00:00  0.0   0.000000   0.000000   0.000000   
...                  ...        ...        ...        ...   
2022-06-06 04:45:00  0.0  83.098106  90.310669  79.928123   
2022-06-06 05:00:00  0.0  82.848106  91.529274  81.146729   
2022-06-06 05:15:00  0.0  83.677292  92.358459  81.975914   
2022-06-06 05:30:00  0.0  84.399185  93.080353  82.697807   
2022-06-06 05:45:00  0.0  85.148819  93.829987  83.447441   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [1, 0, 2, 1]   
...                                    ...           ...   
2022-06-06 04:45:00  [0, 9850, 9849, 9851]  [0, 2, 1, 1]   
2022-06-06 05:00:00  [0, 9850, 9849, 9851]  [0, 1, 1, 1]   
2022-06-06 05:15:00  [0, 9850, 9849, 9851]  [0, 1, 1, 1]   
2022-06-06 05:30:00  [0, 9850, 9849, 9851]  [0, 1, 1, 1]   
2022-06-06 05:45:00  [0, 9850, 9849, 9851]  [0, 1, 1, 1]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, True, False, False] -4.032067    -3.202003   
2022-01-01 00:15:00  [False, True, False, False] -2.921202    -4.678101   
2022-01-01 00:30:00  [False, True, False, False] -3.806861    -4.051631   
2022-01-01 00:45:00  [False, True, False, False] -3.430979    -5.357232   
2022-01-01 01:00:00  [False, True, False, False] -4.392955    -5.831280   
...                                          ...       ...          ...   
2022-06-06 04:45:00    [True, False, True, True]  0.000000    15.000000   
2022-06-06 05:00:00    [True, True, False, True]  0.000000    15.000000   
2022-06-06 05:15:00    [True, True, False, True]  0.000000    15.000000   
2022-06-06 05:30:00    [True, True, False, True]  0.000000    15.000000   
2022-06-06 05:45:00    [True, True, False, True]  0.000000    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -3.202003  
2022-01-01 00:15:00        0.0  -4.678101  
2022-01-01 00:30:00        0.0  -4.051631  
2022-01-01 00:45:00        0.0  -5.357232  
2022-01-01 01:00:00        0.0  -5.831280  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  15.000000  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()